# Summarizing (w/ GPT-2)

## Packages

In [1]:
from utils.json_utils import read_json, write_json
from datasets import Dataset
import pandas as pd

/home/pauli/.local/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Tokenizing

In [2]:
sentences_w_subjects_tokenized = read_json("9_non_lemmatized_tokenized_sentences_black_clover.json")
sentences_w_subjects_tokenized

[{'subjects': ['Yuno'],
  'tokens': ['a',
   'priest',
   'takes',
   'two',
   'babies',
   'abandoned',
   'outside',
   'his',
   'church',
   'inside',
   'and',
   'discovers',
   'two',
   'babies',
   'abandoned',
   'outside',
   'his',
   'church',
   'names',
   'to',
   'be',
   'Yuno',
   'and',
   'Asta',
   '.']},
 {'subjects': ['Asta'],
  'tokens': ['a',
   'priest',
   'takes',
   'two',
   'babies',
   'abandoned',
   'outside',
   'his',
   'church',
   'inside',
   'and',
   'discovers',
   'two',
   'babies',
   'abandoned',
   'outside',
   'his',
   'church',
   'names',
   'to',
   'be',
   'Yuno',
   'and',
   'Asta',
   '.']},
 {'subjects': ['Lily'],
  'tokens': ['Fifteen',
   'years',
   'later',
   ',',
   'Asta',
   'proposes',
   'to',
   'Sister',
   'Lily',
   ',',
   'who',
   'refuses',
   'repeatedly',
   '.']},
 {'subjects': ['Asta'],
  'tokens': ['Fifteen',
   'years',
   'later',
   ',',
   'Asta',
   'proposes',
   'to',
   'Sister',
   'Lily',
   

In [3]:
sentences_w_subjects_tokenized = [
    {
        "subjects" : sentence["subjects"],
        "tokens"  : " ".join(sentence["tokens"])
    } 
    for sentence in sentences_w_subjects_tokenized
]
sentences_w_subjects_tokenized

[{'subjects': ['Yuno'],
  'tokens': 'a priest takes two babies abandoned outside his church inside and discovers two babies abandoned outside his church names to be Yuno and Asta .'},
 {'subjects': ['Asta'],
  'tokens': 'a priest takes two babies abandoned outside his church inside and discovers two babies abandoned outside his church names to be Yuno and Asta .'},
 {'subjects': ['Lily'],
  'tokens': 'Fifteen years later , Asta proposes to Sister Lily , who refuses repeatedly .'},
 {'subjects': ['Asta'],
  'tokens': 'Fifteen years later , Asta proposes to Sister Lily , who refuses repeatedly .'},
 {'subjects': ['Yuno'],
  'tokens': 'Yuno and the other orphans criticize Asta and point out Yuno lack of magic .'},
 {'subjects': ['Asta'],
  'tokens': 'Yuno and the other orphans criticize Asta and point out Yuno lack of magic .'},
 {'subjects': ['Yuno'],
  'tokens': 'Asta tries to show off Asta skills , but Yuno outshines Asta with Asta magic .'},
 {'subjects': ['Asta'],
  'tokens': 'Asta t

In [4]:
max_length = 0
for sentence in sentences_w_subjects_tokenized:
    if len(sentence["tokens"]) > max_length:
        max_length = len(sentence["tokens"])
max_length

610

In [5]:
varied_set_adjectives = read_json("14_varied_set_adjectives_definitions.json")
#varied_set_adjectives

In [6]:
training_sents = list(map(lambda x : x["tokens"], sentences_w_subjects_tokenized))
#training_sents

## Transformer

In [7]:
from transformers import AutoTokenizer, AutoModelForMaskedLM, DataCollatorForLanguageModeling, Trainer, TrainingArguments
import torch

2023-01-26 15:46:07.339643: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-01-26 15:46:07.411895: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-01-26 15:46:07.411908: I tensorflow/compiler/xla/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2023-01-26 15:46:07.801867: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2023-

In [8]:
model_checkpoint = "bert-base-cased"

In [9]:
tokenizer = AutoTokenizer.from_pretrained(model_checkpoint, use_fast=True)

In [10]:
data_collator = DataCollatorForLanguageModeling(tokenizer, mlm=False)

In [11]:
tokenize_fn = lambda doc : tokenizer(
        doc,
        truncation=True,
        max_length=1024
    )

tokenized_dataset = list(map(tokenize_fn, training_sents))

In [12]:
tokenized_dataset = pd.DataFrame(tokenized_dataset)
tokenized_dataset = Dataset.from_pandas(tokenized_dataset)

In [13]:
model = AutoModelForMaskedLM.from_pretrained(
    model_checkpoint, pad_token_id=tokenizer.eos_token_id)

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [14]:
device = f"cuda:{torch.cuda.current_device()}" if torch.cuda.is_available() else "cpu"

In [15]:
training_args = TrainingArguments(
    f"{model_checkpoint}-finetuned-sents-coref-black-clover",
    num_train_epochs=1,
    per_device_train_batch_size=10,
    per_device_eval_batch_size=10,    
    learning_rate=2e-5,
    weight_decay=0.01,
    do_eval=True, # eval en validation set
    evaluation_strategy="steps", # eval en validation set
    eval_steps=100,
    save_steps=100, # checkpoint model every 500 steps
    logging_dir='./logs', # logging
    logging_strategy="steps",
    logging_steps=1,
    fp16=False, # float16 en training (only on CUDA)
    push_to_hub=False,
)

In [16]:
trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=tokenized_dataset, #.select(range(0, 128)),
    eval_dataset=tokenized_dataset, #.select(range(0, 128)),
)

In [17]:
train_output = trainer.train()

/home/pauli/.local/lib/python3.10/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 5989
  Num Epochs = 1
  Instantaneous batch size per device = 10
  Total train batch size (w. parallel, distributed & accumulation) = 10
  Gradient Accumulation steps = 1
  Total optimization steps = 599
  0%|          | 1/599 [00:03<32:21,  3.25s/it]

{'loss': 1.3977, 'learning_rate': 1.996661101836394e-05, 'epoch': 0.0}


  0%|          | 2/599 [00:05<26:53,  2.70s/it]

{'loss': 1.3895, 'learning_rate': 1.993322203672788e-05, 'epoch': 0.0}


  1%|          | 3/599 [00:07<21:28,  2.16s/it]

...

{'loss': 0.0002, 'learning_rate': 6.67779632721202e-08, 'epoch': 1.0}


100%|█████████▉| 598/599 [46:48<00:02,  2.12s/it]

{'loss': 0.0001, 'learning_rate': 3.33889816360601e-08, 'epoch': 1.0}


100%|██████████| 599/599 [46:50<00:00,  1.92s/it]

Training completed. Do not forget to share your model on huggingface.co/models =)


100%|██████████| 599/599 [46:50<00:00,  4.69s/it]

{'loss': 0.0003, 'learning_rate': 0.0, 'epoch': 1.0}
{'train_runtime': 2810.0789, 'train_samples_per_second': 2.131, 'train_steps_per_second': 0.213, 'train_loss': 0.02317726491183841, 'epoch': 1.0}


## Summarize

In [18]:
import numpy as np

In [19]:
def predict_mask(input_str):
    """Tomamos el camino largo en lugar de usar pipeline
    """
    inputs = tokenizer(input_str, return_tensors="pt")
    mask_index = np.where(inputs['input_ids'] == tokenizer.mask_token_id)
    # .eval() to set dropout and batch normalization layers to evaluation mode
    model.eval()
    outputs = model(**inputs)
    top_5_predictions = torch.softmax(outputs.logits[mask_index], dim=1).topk(5)
    predicted = []
    for i in range(5):
        token = tokenizer.decode(top_5_predictions.indices[0, i])
        prob = top_5_predictions.values[0, i]
        predicted.append({
            "token": token, 
            "prob": prob.item()
        })
    return predicted

In [20]:
predicted_by_sentence_by_character = []
for sentence in sentences_w_subjects_tokenized:
    predicted_by_character = dict()
    for subject in sentence["subjects"]:
        print(sentence["tokens"] + " " + subject + " can be described as [MASK].")
        print()
        predicted = predict_mask(sentence["tokens"] + " " + subject + " can be described as [MASK].")
        predicted_by_character[subject] = predicted
        for i in range(0, len(predicted)):
            print(f" {i+1}) {predicted[i]['token']:<20} {predicted[i]['prob']:.3f}")
        print()
    predicted_by_sentence_by_character.append(predicted_by_character)

write_json(predicted_by_sentence_by_character, "27_sent_predicted_by_char_bert_sent_coref.json")

a priest takes two babies abandoned outside his church inside and discovers two babies abandoned outside his church names to be Yuno and Asta . Yuno can be described as [MASK].

 1) [CLS]                0.032
 2) well                 0.024
 3) possessed            0.017
 4) depressed            0.010
 5) mute                 0.007

a priest takes two babies abandoned outside his church inside and discovers two babies abandoned outside his church names to be Yuno and Asta . Asta can be described as [MASK].

 1) [CLS]                0.064
 2) well                 0.028
 3) possessed            0.016
 4) depressed            0.008
 5) normal               0.005

Fifteen years later , Asta proposes to Sister Lily , who refuses repeatedly . Lily can be described as [MASK].

 1) well                 0.015
 2) [CLS]                0.013
 3) female               0.008
 4) depressed            0.008
 5) pregnant             0.007

Fifteen years later , Asta proposes to Sister Lily , who refuses

In [21]:
predicted_by_sentence_by_character

[{'Yuno': [{'token': '[CLS]', 'prob': 0.03198141232132912},
   {'token': 'well', 'prob': 0.024102821946144104},
   {'token': 'possessed', 'prob': 0.016506711021065712},
   {'token': 'depressed', 'prob': 0.01045365072786808},
   {'token': 'mute', 'prob': 0.006880167406052351}]},
 {'Asta': [{'token': '[CLS]', 'prob': 0.06378690898418427},
   {'token': 'well', 'prob': 0.027626674622297287},
   {'token': 'possessed', 'prob': 0.015696875751018524},
   {'token': 'depressed', 'prob': 0.007910224609076977},
   {'token': 'normal', 'prob': 0.005311070941388607}]},
 {'Lily': [{'token': 'well', 'prob': 0.014730491675436497},
   {'token': '[CLS]', 'prob': 0.013179894536733627},
   {'token': 'female', 'prob': 0.008496018126606941},
   {'token': 'depressed', 'prob': 0.007985766045749187},
   {'token': 'pregnant', 'prob': 0.0073789628222584724}]},
 {'Asta': [{'token': '[CLS]', 'prob': 0.02613426186144352},
   {'token': 'well', 'prob': 0.018935659900307655},
   {'token': 'depressed', 'prob': 0.01357097

In [22]:
predicted_by_sentence_by_character = []
for sentence in sentences_w_subjects_tokenized:
    predicted_by_character = dict()
    for subject in sentence["subjects"]:
        print(subject + " can be described as [MASK].")
        print()
        predicted = predict_mask(subject + " can be described as [MASK].")
        predicted_by_character[subject] = predicted
        for i in range(0, len(predicted)):
            print(f" {i+1}) {predicted[i]['token']:<20} {predicted[i]['prob']:.3f}")
        print()
    predicted_by_sentence_by_character.append(predicted_by_character)

write_json(predicted_by_sentence_by_character, "27_predicted_by_char_bert_sent_coref.json")

Yuno can be described as [MASK].

 1) well                 0.061
 2) [CLS]                0.044
 3) depressed            0.007
 4) possessed            0.005
 5) drunk                0.005

Asta can be described as [MASK].

 1) well                 0.097
 2) [CLS]                0.053
 3) follows              0.007
 4) opposed              0.005
 5) normal               0.003

Lily can be described as [MASK].

 1) well                 0.030
 2) Lily                 0.030
 3) [CLS]                0.026
 4) female               0.008
 5) feminine             0.007

Asta can be described as [MASK].

 1) well                 0.097
 2) [CLS]                0.053
 3) follows              0.007
 4) opposed              0.005
 5) normal               0.003

Yuno can be described as [MASK].

 1) well                 0.061
 2) [CLS]                0.044
 3) depressed            0.007
 4) possessed            0.005
 5) drunk                0.005

Asta can be described as [MASK].

 1) well        

In [23]:
predicted_by_sentence_by_character

[{'Yuno': [{'token': 'well', 'prob': 0.061498939990997314},
   {'token': '[CLS]', 'prob': 0.04403240606188774},
   {'token': 'depressed', 'prob': 0.006903379689902067},
   {'token': 'possessed', 'prob': 0.004973285365849733},
   {'token': 'drunk', 'prob': 0.004861949011683464}]},
 {'Asta': [{'token': 'well', 'prob': 0.09666887670755386},
   {'token': '[CLS]', 'prob': 0.052952952682971954},
   {'token': 'follows', 'prob': 0.006803152617067099},
   {'token': 'opposed', 'prob': 0.004629872739315033},
   {'token': 'normal', 'prob': 0.0033788199070841074}]},
 {'Lily': [{'token': 'well', 'prob': 0.030192334204912186},
   {'token': 'Lily', 'prob': 0.02950207330286503},
   {'token': '[CLS]', 'prob': 0.025733662769198418},
   {'token': 'female', 'prob': 0.00785995926707983},
   {'token': 'feminine', 'prob': 0.0066382004879415035}]},
 {'Asta': [{'token': 'well', 'prob': 0.09666887670755386},
   {'token': '[CLS]', 'prob': 0.052952952682971954},
   {'token': 'follows', 'prob': 0.006803152617067099

In [25]:
def predict_mask_x(input_str, x):
    """Tomamos el camino largo en lugar de usar pipeline
    """
    inputs = tokenizer(input_str, return_tensors="pt")
    mask_index = np.where(inputs['input_ids'] == tokenizer.mask_token_id)
    # .eval() to set dropout and batch normalization layers to evaluation mode
    model.eval()
    outputs = model(**inputs)
    top_x_predictions = torch.softmax(outputs.logits[mask_index], dim=1).topk(x)
    predicted = []
    for i in range(x):
        token = tokenizer.decode(top_x_predictions.indices[0, i])
        prob = top_x_predictions.values[0, i]
        predicted.append({
            "token": token, 
            "prob": prob.item()
        })
    return predicted

In [29]:
subject = "Yami"
predicted = predict_mask_x(subject + " can be described as [MASK].", 27)
predicted_by_character[subject] = predicted
for i in range(0, len(predicted)):
    print(f" {i+1}) {predicted[i]['token']:<20} {predicted[i]['prob']:.3f}")
print()

 1) [CLS]                0.045
 2) well                 0.041
 3) depressed            0.004
 4) normal               0.004
 5) sound                0.004
 6) opposed              0.004
 7) floating             0.004
 8) possessed            0.003
 9) falling              0.003
 10) distinct             0.003
 11) weak                 0.003
 12) hollow               0.003
 13) stable               0.002
 14) follows              0.002
 15) nothing              0.002
 16) either               0.002
 17) simple               0.002
 18) strong               0.002
 19) drunk                0.002
 20) [UNK]                0.002
 21) flying               0.002
 22) independent          0.002
 23) impossible           0.002
 24) real                 0.002
 25) smoke                0.002
 26) mobile               0.001
 27) true                 0.001

